# Build a tile index (`tindex`) for a set of DPS output

In [1]:
#!pip install cogeo_mosaic

In [35]:
import cogeo_mosaic
cogeo_mosaic.__version__ # 8.1.0 on pangeo_v3.1.4 got this working again

'8.1.0'

In [17]:
from maap.maap import MAAP
maap = MAAP()

In [18]:
ICESAT2_BOREAL_REPO_PATH = '/projects/code/icesat2_boreal'     
ICESAT2_BOREAL_LIB_PATH = ICESAT2_BOREAL_REPO_PATH + '/lib'

In [19]:
import geopandas as gpd
import pandas as pd
import os

import sys
import s3fs

sys.path.append(ICESAT2_BOREAL_LIB_PATH)

print("Importing packages complete.")

Importing packages complete.


In [107]:
import importlib
import mosaiclib
import maplib_folium
importlib.reload(mosaiclib)
importlib.reload(maplib_folium)

<module 'maplib_folium' from '/projects/code/icesat2_boreal/lib/maplib_folium.py'>

In [21]:
import mosaiclib
from mosaiclib import *

In [45]:
DICT_BUILD_TINDEX_

NameError: name 'DICT_BUILD_TINDEX_LC' is not defined

## Build new tindex and MosiacJSONs

In [23]:
DICT_BUILD_TINDEX_ATL08_FILT = {
  'SET': 'ATL08',
 'USER': 'montesano',
 'ALG_NAME': 'run_extract_atl08_covars', 
 'ALG_VERSION': 'extract_atl08_covars',
 'VAR': 'ATL08_filt_extract',
 'BATCH_NAME': '2024',
 'YEAR_LIST': '2024 2025',
 #'DPS_MONTH_LIST': '02 03 10',
 'DPS_MONTH_LIST': '01 02 03 04 05 06 07 08 09 10 11 12',
 'DPS_DAY_MIN': 1,
 'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/boreal_tiles_v004_model_ready.gpkg'
}

In [126]:
DICT_BUILD_TINDEX_HLS = {
  'SET': 'HLS',
 'USER': 'montesano',
 'ALG_NAME': "do_HLS_stack_3-1-2", 
 'ALG_VERSION': 'HLS_stack_2023_v1',
 'VAR': 'HLS',
 'BATCH_NAME': 'HLSCONUS_H30_2024',
 'YEAR_LIST': '2025',
 #'DPS_MONTH_LIST': '02 03 10',
'DPS_MONTH_LIST': '01 02 03 04 05',
# 'DPS_MONTH_LIST': '01 02 03 04 05 06 07 08 09 10 11 12',
 'DPS_DAY_MIN': 1,
 #'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/boreal_tiles_v004_model_ready.gpkg'
    'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/tile_grid_americas.gpkg'
}

In [127]:
DICT_BUILD_TINDEX_GLO30CONUS = {
 'SET': 'TOPO',
 'USER': 'montesano',
 'ALG_NAME': 'run_build_stack_topo',
 'ALG_VERSION': 'build_stack_v2024_2',
 'VAR': 'Topo',
 'BATCH_NAME': 'CopernicusGLO30CONUS',
 'YEAR_LIST': '2025',
 'DPS_MONTH_LIST': '03',
 'DPS_DAY_MIN': 1,
 'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/tile_grid_americas.gpkg'}

In [128]:
DICT_BUILD_TINDEX_LCCONUS = {
 'SET': 'run_build_stack',
 'USER': 'montesano',
 'ALG_NAME': 'run_build_stack',
 'ALG_VERSION': 'build_stack_v2023_2',
 'VAR': 'LC',
 'BATCH_NAME': 'LCCONUS_ESA_WC_2020',
 'YEAR_LIST': '2025',
 'DPS_MONTH_LIST': '03',
 'DPS_DAY_MIN': 1,
 'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/tile_grid_americas.gpkg'}

In [59]:
DICT_BUILD_TINDEX_AGB = {
    'SET' : 'BOREAL_MAP',#'BOREAL_MAP_TEST',
    'USER' : 'aliz237', #'lduncanson', dps_output/run_boreal_biomass_map/dev/AGB_H30_2020/test1/
    'ALG_NAME' : 'run_boreal_biomass_map',
    'ALG_VERSION' : 'dev_v1.5', #'test-ranger',#'sar_dev', #'boreal_agb_2024_v6',  /run_boreal_biomass_map/dev_v1.5/AGB_H30_2020/test_with_sar/
    'VAR' : 'AGB',
    'BATCH_NAME' : 'AGB_H30_2024/full_run_no_uncert', #'AGB_H30_2020/full_run', #'AGB_S1H30_2020/full_run_no_uncert', #'AGB_S1H30_2020/AGU24', #'AGB_H30_2020/no_uncertainty_sar', #'AGB_H30_2020/Version2_SD',
    'YEAR_LIST': '2025',
    'DPS_MONTH_LIST' : '01 02 03 04 05 06 07 08 09 10 11 12', #'07 08 09 10',        
    'DPS_DAY_MIN' : 1 ,
    'TILES_INDEX_PATH': boreal_tile_index_path
}

In [60]:
DICT_BUILD_TINDEX_HT = {
    'SET' : 'BOREAL_MAP',
    'USER' : 'aliz237', #'lduncanson'
    'ALG_NAME' : 'run_boreal_biomass_map',
    'ALG_VERSION' : 'dev_v1.5', #'boreal_agb_2024_v6', 
    'VAR' : 'HT',
    'BATCH_NAME' : 'Ht_H30_2020/full_run',
    'YEAR_LIST': '2025',
    'DPS_MONTH_LIST' : '01',        
    'DPS_DAY_MIN' : 1 ,
    'TILES_INDEX_PATH': boreal_tile_index_path
}

In [69]:
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_ATL08_FILT
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_AGB #DICT_BUILD_TINDEX_HT #
# DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_FORESTAGE100m #DICT_BUILD_TINDEX_AGB #
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_HLS

In [68]:
DICT_BUILD_TINDEX = mosaiclib.DICT_BUILD_TINDEX_TCC2020
DICT_BUILD_TINDEX = mosaiclib.DICT_BUILD_TINDEX_TCCTREND2020
DICT_BUILD_TINDEX = mosaiclib.DICT_BUILD_TINDEX_FORESTAGE2020

In [133]:
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_HLS

In [129]:
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_GLO30CONUS
DICT_BUILD_TINDEX = DICT_BUILD_TINDEX_LCCONUS

In [130]:
DICT_BUILD_TINDEX

{'SET': 'run_build_stack',
 'USER': 'montesano',
 'ALG_NAME': 'run_build_stack',
 'ALG_VERSION': 'build_stack_v2023_2',
 'VAR': 'LC',
 'BATCH_NAME': 'LCCONUS_ESA_WC_2020',
 'YEAR_LIST': '2025',
 'DPS_MONTH_LIST': '03',
 'DPS_DAY_MIN': 1,
 'TILES_INDEX_PATH': '/projects/shared-buckets/montesano/databank/tile_grid_americas.gpkg'}

In [134]:
ENV = 'pangeo' #'pangeo' #'python'

In [ ]:
%%time
if True:
    DPS_IDENTIFIER = f"{DICT_BUILD_TINDEX['ALG_VERSION']}/{DICT_BUILD_TINDEX['BATCH_NAME']}"

    OUTDIR = f"/projects/my-public-bucket/DPS_tile_lists/{DICT_BUILD_TINDEX['SET']}/{DPS_IDENTIFIER}"
    !mkdir -p $OUTDIR

    # Build tindex
    args = f"--RETURN_DUPS --user {DICT_BUILD_TINDEX['USER']} --dps_identifier {DPS_IDENTIFIER} \
    -alg_name {DICT_BUILD_TINDEX['ALG_NAME']} -t {DICT_BUILD_TINDEX['VAR']} -y_list {DICT_BUILD_TINDEX['YEAR_LIST']} \
    --dps_month_list {DICT_BUILD_TINDEX['DPS_MONTH_LIST']} -d_min {DICT_BUILD_TINDEX['DPS_DAY_MIN']} --outdir {OUTDIR} \
    -boreal_tile_index_path {DICT_BUILD_TINDEX['TILES_INDEX_PATH']}"

    cmd = f"/opt/conda/envs/{ENV}/bin/python /projects/code/icesat2_boreal/lib/build_tindex_master.py {args} --WRITE_TINDEX_MATCHES_GDF"
    !echo $cmd
    !eval $cmd

/opt/conda/envs/pangeo/bin/python /projects/code/icesat2_boreal/lib/build_tindex_master.py --RETURN_DUPS --user montesano --dps_identifier HLS_stack_2023_v1/HLSCONUS_H30_2024 -alg_name do_HLS_stack_3-1-2 -t HLS -y_list 2025 --dps_month_list 01 02 03 04 05 -d_min 1 --outdir /projects/my-public-bucket/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLSCONUS_H30_2024 -boreal_tile_index_path /projects/shared-buckets/montesano/databank/tile_grid_americas.gpkg --WRITE_TINDEX_MATCHES_GDF
NASA MAAP
INFO: Pandarallel will run on 25 workers.
INFO: Pandarallel will use Memory file system to transfer data between the main process and workers.
NASA MAAP

Building a list of tiles:
DPS ID:		HLS_stack_2023_v1/HLSCONUS_H30_2024
Type:		HLS
Year:		['2025']
Month:		['01', '02', '03', '04', '05']
Days:		1-31

Output dir:  /projects/my-public-bucket/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLSCONUS_H30_2024
Rows before NaN removal: 476
Paths creating null tile_nums: []
Rows after NaN removal: 476

No duplicates found.

# 

In [78]:
#!aws s3 rm --recursive s3://maap-ops-workspace/montesano/dps_output/do_HLS_stack_3-1-2/HLS_stack_2023_v1/HLSCONUS_H30_2024/mc0_mn50_07-01_08-31_2024_2024/2025/03/06/09

In [89]:
import s3fs
s3 = s3fs.S3FileSystem(anon=True)

### Check the tindex

In [103]:
#tindex = gpd.read_file('/projects/my-public-bucket/DPS_tile_lists/FORESTAGE100m/tile_forestage_v1/forestage_2020/FORESTAGE100m_tindex_master.gpkg')
tindex = gpd.read_file('/projects/my-public-bucket/DPS_tile_lists/TOPO/build_stack_v2024_2/CopernicusGLO30CONUS/Topo_tindex_master.gpkg')
#print(tindex.tile_num.to_list())
#tindex.explore()
tindex.head()

area_sq_km                      name continent            region  tile_num  \
0      8100.0                    Canada  Americas  Northern America      1687   
1      8100.0  United States of America  Americas  Northern America      1683   
2      8100.0  United States of America  Americas  Northern America      1577   
3      8100.0  United States of America  Americas  Northern America       988   
4      8100.0  United States of America  Americas  Northern America      1682   

                                             s3_path  \
0  s3://maap-ops-workspace/montesano/dps_output/r...   
1  s3://maap-ops-workspace/montesano/dps_output/r...   
2  s3://maap-ops-workspace/montesano/dps_output/r...   
3  s3://maap-ops-workspace/montesano/dps_output/r...   
4  s3://maap-ops-workspace/montesano/dps_output/r...   

                                          local_path  \
0  /projects/my-private-bucket/dps_output/run_bui...   
1  /projects/my-private-bucket/dps_output/run_bui...   
2  /projects/my-private-bucket/dps_output/run_bui...   
3  /projects/my-private-bucket/dps_output/run_bui...   
4  /projects/my-private-bucket/dps_output/run_bui...   

                                            geometry  
0  POLYGON ((2016299.782 2439880.791, 2016299.782...  
1  POLYGON ((2016299.782 2079880.791, 2016299.782...  
2  POLYGON ((1746299.782 1539880.791, 1746299.782...  
3  POLYGON ((306299.782 999880.791, 306299.782 10...  
4  POLYGON ((2016299.782 1989880.791, 2016299.782...

In [104]:
boreal_tiles = gpd.read_file(boreal_tile_index_path.replace('.gpkg','_model_ready.gpkg'))
tile_grid = gpd.read_file('/projects/shared-buckets/montesano/databank/tile_grid_conus.gpkg')

In [107]:
TILES_LIST = boreal_tiles.tile_num.to_list()
print(len(TILES_LIST))
boreal_tiles.shape

4956


(4956, 6)

In [110]:
TILES_LIST = tile_grid.tile_num.to_list()
print(len(TILES_LIST))
tile_grid.shape

1178


(1178, 6)

In [109]:
fn_list = [
            mosaiclib.HT_MOSAIC_JSON_FN_DICT['2020_v2.0'].replace('_mosaic.json','.csv'),
            mosaiclib.HT_MOSAIC_JSON_FN_DICT['2020_v2.1'].replace('_mosaic.json','.csv'),
            mosaiclib.HT_MOSAIC_JSON_FN_DICT['2020_v2.2'].replace('_mosaic.json','.csv'),
            mosaiclib.AGB_MOSAIC_JSON_FN_DICT['2020_v2.0'].replace('_mosaic.json','.csv'),
            mosaiclib.AGB_MOSAIC_JSON_FN_DICT['2020_v2.1'].replace('_mosaic.json','.csv'),
            mosaiclib.AGB_MOSAIC_JSON_FN_DICT['2020_v2.2'].replace('_mosaic.json','.csv'),
            mosaiclib.HLS_MOSAIC_JSON_FN_DICT['2020'].replace('_mosaic.json','.csv')
]
fn_list

['s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/boreal_agb_2024_v6/Ht_H30_2020/Version2_SD/HT_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/Ht_H30_2020/full_run/HT_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/Ht_S1H30_2020/full_run_no_uncert/HT_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/boreal_agb_2024_v6/AGB_H30_2020/Version2_SD/AGB_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/AGB_H30_2020/full_run/AGB_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/AGB_S1H30_2020/full_run_no_uncert/AGB_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLS_H30_2020/HLS_tindex_master.csv']

In [108]:
fn_list = [
            mosaiclib.TOPO_MOSAIC_JSON_FN_DICT['2020CONUS'].replace('_mosaic.json','.csv'),
            mosaiclib.LC_MOSAIC_JSON_FN_DICT['2020CONUS'].replace('_mosaic.json','.csv'),
            mosaiclib.HLS_MOSAIC_JSON_FN_DICT['2024CONUS'].replace('_mosaic.json','.csv')
]
fn_list

['s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/TOPO/build_stack_v2024_2/CopernicusGLO30CONUS/Topo_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack/build_stack_v2023_2/LCCONUS_ESA_WC_2020/LC_tindex_master.csv',
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLSCONUS_H30_2024/HLS_tindex_master.csv']

In [111]:
DICT_NEEDS = dict()
for fn in fn_list:
    print(fn)
    tindex = pd.read_csv(fn)
    print(tindex.shape)
    print(f'{tile_grid.shape[0]-tindex.shape[0]} missing.')

    #TILES_LIST
    NEED_LIST = list(set(TILES_LIST)-set(tindex.tile_num.to_list()))
    print(NEED_LIST,'\n')
    DICT_NEEDS.update({fn: NEED_LIST})

s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/TOPO/build_stack_v2024_2/CopernicusGLO30CONUS/Topo_tindex_master.csv
(1157, 6)
21 missing.
[263, 777, 150, 1181, 162, 38, 1064, 1320, 46, 305, 566, 826, 198, 1483, 83, 984, 90, 109, 371, 249, 1146] 

s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack/build_stack_v2023_2/LCCONUS_ESA_WC_2020/LC_tindex_master.csv
(1158, 6)
20 missing.
[265, 23, 166, 682, 299, 172, 301, 686, 687, 304, 306, 313, 703, 704, 198, 602, 93, 98, 612, 370] 

s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLSCONUS_H30_2024/HLS_tindex_master.csv
(187, 6)
991 missing.
[76, 77, 95, 96, 99, 104, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 134, 135, 147, 150, 151, 154, 161, 163, 164, 170, 172, 178, 203, 230, 270, 274, 276, 278, 279, 280, 281, 282, 292, 293, 294, 295, 296, 297, 298, 299, 300, 301, 302, 303, 304, 305, 306, 307, 308, 309, 310, 311, 312, 313, 314, 315, 324

In [93]:
DICT_NEEDS

{'s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/boreal_agb_2024_v6/Ht_H30_2020/Version2_SD/HT_tindex_master.csv': [23497,
  23498,
  23499,
  45970,
  22937,
  22938],
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/Ht_H30_2020/full_run/HT_tindex_master.csv': [1735,
  1802,
  45970,
  23827,
  35060,
  4411,
  2302],
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/Ht_S1H30_2020/full_run_no_uncert/HT_tindex_master.csv': [23776,
  23777,
  23778,
  23779,
  23780,
  23497,
  22937,
  23498,
  23499,
  23217,
  45970,
  23218,
  35060,
  23219,
  42745,
  22938,
  4411],
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/boreal_agb_2024_v6/AGB_H30_2020/Version2_SD/AGB_tindex_master.csv': [45970,
  23827],
 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/BOREAL_MAP/dev_v1.5/AGB_H30_2020/full_run/AGB_tindex_master.csv': [1735,
  1802,
  45970,
  23827,
  35060,
  4411,
  39261],
 's3:

In [38]:
tindex_tcctrend = pd.read_csv(fn_tcctrend)

In [39]:
tindex_ht.shape

(4950, 5)

In [40]:
tindex_agb.shape

(4954, 5)

In [21]:
TP_TILES_LIST = tindex_age.tile_num.to_list() + tindex_tcctrend.tile_num.to_list() + tindex_age.tile_num.to_list()
len(list(set(TP_TILES_LIST)))

3345

In [22]:
# Age tiles not in TP tile list yet
NEED_LIST_AGE = list(set(TP_TILES_LIST)-set(tindex_age.tile_num.to_list()))
print(NEED_LIST_AGE)

[]


In [42]:
# trend tiles not in TP tile list yet
NEED_LIST_TCCTREND = list(set(TP_TILES_LIST)-set(tindex_tcctrend.tile_num.to_list()))
print(NEED_LIST_TCCTREND)

[]


In [44]:
# TCC tiles not in TP tile list yet
NEED_LIST_TCC2020 = list(set(TP_TILES_LIST)-set(tindex_tcc2020.tile_num.to_list()))
print(len(NEED_LIST_TCC2020))

283


In [101]:
boreal_tiles_need = boreal_tiles[boreal_tiles.tile_num.isin([39621] )]
boreal_tiles_need.explore()

ValueError: Location values cannot contain NaNs.

In [41]:
boreal_tiles_age = boreal_tiles[boreal_tiles.tile_num.isin(list(set(TP_TILES_LIST)) )]
boreal_tiles_age.explore()

In [35]:
boreal_tiles_tcctrend = boreal_tiles[boreal_tiles.tile_num.isin(tindex_tcctrend.tile_num.to_list())]
boreal_tiles_tcctrend.explore()

In [27]:
boreal_tiles[~boreal_tiles.tile_num.isin(tindex_age.tile_num.to_list())]

In [ ]:
MISSING_LIST_AGB = boreal_tiles[~boreal_tiles.tile_num.isin(tindex_agb.tile_num.to_list())].tile_num.to_list()
MISSING_LIST_AGB

In [ ]:
MISSING_LIST_HT = boreal_tiles[~boreal_tiles.tile_num.isin(tindex_ht.tile_num.to_list())].tile_num.to_list()
MISSING_LIST_HT

In [ ]:
ATL08_FILT_TINDEX_FN_DICT['2020']

In [ ]:
tindex_atl08 = pd.read_csv(ATL08_FILT_TINDEX_FN_DICT['2020'])
ATL08_TILES = tindex_atl08.tile_num.to_list()
len(ATL08_TILES)

In [ ]:
tindex_atl08[tindex_atl08.tile_num.isin([23497, 23498, 23499])]

In [ ]:
tindex_agb[tindex_agb.tile_num == 22937].s3_path.to_list()[0]

In [ ]:
#boreal_tiles.explore(m=boreal_tiles_orig[boreal_tiles_orig.tile_num.isin(NEED_LIST)].explore(color='red'))

In [ ]:
s3 = s3fs.S3FileSystem(anon=True)